In [0]:
!pip install -qq -U cufflinks

In [0]:
import tensorflow as tf
import os

In [3]:
if tf.gfile.Exists('./fenwicks'):
  tf.gfile.DeleteRecursively('./fenwicks')
!git clone https://github.com/fenwickslab/fenwicks.git

import fenwicks as fw

Cloning into 'fenwicks'...
remote: Enumerating objects: 152, done.
remote: Counting objects: 100% (152/152), done.
remote: Compressing objects: 100% (105/105), done.
remote: Total 1373 (delta 95), reused 101 (delta 46), pack-reused 1221
Receiving objects: 100% (1373/1373), 36.03 MiB | 15.37 MiB/s, done.
Resolving deltas: 100% (828/828), done.


In [4]:
BUCKET = 'gs://gs_colab'
PROJECT = 'tutorial8'
MODEL = "ResNet50" #@param ["InceptionResNetV2", "ResNet50", "ResNet50V2", "InceptionV3", "MobileNetV2", "Xception"]

BATCH_SIZE = 128 #@param ["128", "256", "512"] {type:"raw"}
EPOCHS = 10 #@param {type:"slider", min:0, max:50, step:1}
LEARNING_RATE = 0.001 #@param ["0.001", "0.01"] {type:"raw"}
WARMUP = 0.2 #@param {type:"slider", min:0, max:0.5, step:0.05}
WEIGHT_DECAY = 0.000125 #@param ["0.000125", "0.00025", "0.0005", "0.0"] {type:"raw"}


In [5]:
fw.colab_utils.setup_gcs()

In [6]:
data_dir, work_dir = fw.io.get_gcs_dirs(BUCKET, PROJECT)

In [7]:
base_model = fw.keras_models.get_model(MODEL, BUCKET)

In [8]:
data_dir_local = fw.datasets.untar_data(fw.datasets.URLs.PETS, os.path.join('.', PROJECT))
data_dir_local = os.path.join(data_dir_local, 'oxford-iiit-pet/images')
data_dir_local

811712512/811706944 [==============================] - 15s 0us/step


'./tutorial8/datasets/oxford-iiit-pet/images'

In [9]:
fw.preprocess.check_rgb(data_dir_local)

ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Egyptian_Mau_139.jpg is not an RGB image but of mode: P. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Egyptian_Mau_177.jpg is not an RGB image but of mode: P. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Abyssinian_34.jpg is not an RGB image but of mode: P. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Egyptian_Mau_14.jpg is not an RGB image but of mode: RGBA. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Abyssinian_5.jpg is not an RGB image but of mode: RGBA. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Egyptian_Mau_129.jpg is not an RGB image but of mode: L. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Egyptian_Mau_145.jpg is not an RGB image but of mode: P. Fixing it now.
ERROR:tensorflow:./tutorial8/datasets/oxford-iiit-pet/images/Egyptian_M

In [10]:
train_fn = os.path.join(data_dir, 'train.tfrec')
valid_fn = os.path.join(data_dir, 'test.tfrec')
pat = r'/([^/]+)_\d+.jpg$'
paths_train, paths_test, y_train, y_test, labels = fw.data.data_dir_re_tfrecord_split(
  data_dir_local, pat, train_fn, valid_fn)

n_train, n_test = len(y_train), len(y_test)
n_classes = len(labels)

INFO:tensorflow:Output file already exists. Skipping.
INFO:tensorflow:Output file already exists. Skipping.


In [11]:
fw.plt.plot_counts_pie(y_train, labels, width=550)

In [12]:
def build_nn():
  base = base_model.model_func()
  base.trainable = False  
  model = fw.Sequential()
  model.add(base)
  model.add(fw.layers.FastAiHead(n_classes))
  return model

In [13]:
# test_output = fw.layers.check_model(build_nn, base_model.img_size, base_model.img_size)
# test_output

In [14]:
steps_per_epoch = n_train // BATCH_SIZE
total_steps = steps_per_epoch * EPOCHS
warmup_steps = int(total_steps * WARMUP)

In [15]:
cosine_decay = tf.train.cosine_decay_restarts
lr_func = fw.train.one_cycle_lr(LEARNING_RATE, total_steps, warmup_steps, cosine_decay)
fw.plt.plot_lr_func(lr_func, total_steps)

Instructions for updating:
Colocations handled automatically by placer.


In [16]:
opt_func = fw.train.adam_wd_optimizer(lr_func, wd=WEIGHT_DECAY)
model_func = fw.train.get_clf_model_func(build_nn, opt_func)

In [17]:
def get_input_func(fn, training, tfms_func):
  h = w = base_model.img_size
  tfms = tfms_func(h, w, training, normalizer=base_model.normalizer)
  parser = fw.data.get_tfexample_image_parser(tfms)
  return lambda params: fw.data.tfrecord_ds(fn, parser, params['batch_size'], training=training)

In [18]:
train_input_func = get_input_func(train_fn, True, fw.transform.get_inception_transforms)
valid_input_func = get_input_func(valid_fn, False, fw.transform.get_inception_transforms)

In [19]:
est = fw.train.get_tpu_estimator(steps_per_epoch, model_func, work_dir, 
  base_model.weight_dir, base_model.weight_vars, trn_bs=BATCH_SIZE, val_bs = n_test)

INFO:tensorflow:Using config: {'_model_dir': 'gs://gs_colab/work/tutorial8/2019-05-10-19:58:40', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
cluster_def {
  job {
    name: "worker"
    tasks {
      key: 0
      value: "10.39.209.98:8470"
    }
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': None, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f27bf10ef98>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': 'grpc://10.39.209.98:8470', '_evaluation_master': 'grpc://10.39.209.98:8470', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1, '_tpu_config': TPUConfig(iterations_per_loop=46, num_shards=None

In [20]:
est.train(train_input_func, steps=total_steps)

INFO:tensorflow:Querying Tensorflow master (grpc://10.39.209.98:8470) for TPU system metadata.
INFO:tensorflow:Found TPU system:
INFO:tensorflow:*** Num TPU Cores: 8
INFO:tensorflow:*** Num TPU Workers: 1
INFO:tensorflow:*** Num TPU Cores Per Worker: 8
INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:CPU:0, CPU, -1, 15602626529017716015)
INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:XLA_CPU:0, XLA_CPU, 17179869184, 4409931473799665923)
INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:TPU:0, TPU, 17179869184, 7580668119931391688)
INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:TPU:1, TPU, 17179869184, 1343468783363627222)
INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:TPU:2, TPU, 17179869184, 16456176570627325505)
INFO:tensorflow:*** Available Device: _DeviceAttributes(

/usr/local/lib/python3.6/dist-packages/keras_applications/resnet50.py:265: UserWarning:

The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.



Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Use tf.cast instead.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Warm-starting with WarmStartSettings: WarmStartSettings(ckpt_to_initialize_from='gs://gs_colab/model/ResNet50/keras', vars_to_warm_start=['res5c_branch2c/bias[^/]', 'res5c_branch2b/kernel[^/]', 'res5c_branch2b/bias[^/]', 'res5c_branch2a/kernel[^/]', 'res5a_branch2a/bias[^/]', 'res5a_branch1/bias[^/]', 'res4f_branch2c/bias[^/]', 'res4f_branch2b/kernel[^/]', 'res4f_branch2a/bias[^/]', 'res4e_branch2a/bias[^/]', 'res4d_branch2c/kernel[^/]', 'res4d_branch2c/bias[^/]', 'res4d_branch2b/kernel[^/]', 'res4d_branch2b/bias[^/]', 'res4d_branch2a/kernel[^/]', 'res4d_branch2a/bias[^/]', 'res4c_branch2c/kernel[^/]', 'res4c_branch2c/bias[^/]', 'res4c_branch2b/kernel[^/]', 'res4c_branch2b/bias[^/]

In [21]:
result = est.evaluate(valid_input_func, steps=1)

INFO:tensorflow:Calling model_fn.
ERROR:tensorflow:Operation of type Placeholder (input_1) is not supported on the TPU. Execution will fail if this op is used in the graph. 


/usr/local/lib/python3.6/dist-packages/keras_applications/resnet50.py:265: UserWarning:

The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.



Instructions for updating:
Deprecated in favor of operator or tf.math.divide.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2019-05-10T20:00:20Z
INFO:tensorflow:TPU job name worker
INFO:tensorflow:Graph was finalized.
Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from gs://gs_colab/work/tutorial8/2019-05-10-19:58:40/model.ckpt-460
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Init TPU system
INFO:tensorflow:Initialized TPU in 10 seconds
INFO:tensorflow:Starting infeed thread controller.
INFO:tensorflow:Starting outfeed thread controller.
INFO:tensorflow:Initialized dataset iterators in 0 seconds
INFO:tensorflow:Enqueue next (1) batch(es) of data to infeed.
INFO:tensorflow:Dequeue next (1) batch(es) of data from outfeed.
INFO:tensorflow:Evaluation [1/1]
INFO:tensorflow:Stop infeed thread controller
INFO:tensorflow:Shutting dow

In [22]:
fw.io.create_clean_dir(work_dir)

In [23]:
reverse_normalizer = fw.transform.REVERSE_IMAGENET_NORMALIZE[base_model.normalizer]
fw.anim.show_input_func(train_input_func, n_img=20, converter=reverse_normalizer)

In [24]:
train_input_func = get_input_func(train_fn, True, fw.transform.get_fastai_transforms)
valid_input_func = get_input_func(valid_fn, False, fw.transform.get_fastai_transforms)

In [25]:
est.train(train_input_func, steps=total_steps)

INFO:tensorflow:Calling model_fn.
ERROR:tensorflow:Operation of type Placeholder (input_1) is not supported on the TPU. Execution will fail if this op is used in the graph. 


/usr/local/lib/python3.6/dist-packages/keras_applications/resnet50.py:265: UserWarning:

The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.



INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Warm-starting with WarmStartSettings: WarmStartSettings(ckpt_to_initialize_from='gs://gs_colab/model/ResNet50/keras', vars_to_warm_start=['res5c_branch2c/bias[^/]', 'res5c_branch2b/kernel[^/]', 'res5c_branch2b/bias[^/]', 'res5c_branch2a/kernel[^/]', 'res5a_branch2a/bias[^/]', 'res5a_branch1/bias[^/]', 'res4f_branch2c/bias[^/]', 'res4f_branch2b/kernel[^/]', 'res4f_branch2a/bias[^/]', 'res4e_branch2a/bias[^/]', 'res4d_branch2c/kernel[^/]', 'res4d_branch2c/bias[^/]', 'res4d_branch2b/kernel[^/]', 'res4d_branch2b/bias[^/]', 'res4d_branch2a/kernel[^/]', 'res4d_branch2a/bias[^/]', 'res4c_branch2c/kernel[^/]', 'res4c_branch2c/bias[^/]', 'res4c_branch2b/kernel[^/]', 'res4c_branch2b/bias[^/]', 'res4c_branch2a/bias[^/]', 'res4b_branch2b/bias[^/]', 'res4a_branch2c/kernel[^/]', 'res4a_branch2c/bias[^/]', 'res4a_branch2b/kernel[^/]', 'res4a_branch2b/bias[^/]', 'res4a_branch2a/bias[^/]', 'res4a_branch1/

In [26]:
result = est.evaluate(valid_input_func, steps=1)

INFO:tensorflow:Calling model_fn.
ERROR:tensorflow:Operation of type Placeholder (input_1) is not supported on the TPU. Execution will fail if this op is used in the graph. 


/usr/local/lib/python3.6/dist-packages/keras_applications/resnet50.py:265: UserWarning:

The output shape of `ResNet50(include_top=False)` has been changed since Keras 2.2.0.



INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2019-05-10T20:05:00Z
INFO:tensorflow:TPU job name worker
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from gs://gs_colab/work/tutorial8/2019-05-10-19:58:40/model.ckpt-460
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Init TPU system
INFO:tensorflow:Initialized TPU in 9 seconds
INFO:tensorflow:Starting infeed thread controller.
INFO:tensorflow:Starting outfeed thread controller.
INFO:tensorflow:Initialized dataset iterators in 0 seconds
INFO:tensorflow:Enqueue next (1) batch(es) of data to infeed.
INFO:tensorflow:Dequeue next (1) batch(es) of data from outfeed.
INFO:tensorflow:Evaluation [1/1]
INFO:tensorflow:Stop infeed thread controller
INFO:tensorflow:Shutting down InfeedController thread.
INFO:tensorflow:InfeedController received shutdown signal, stopping.
INFO:tensorflow:Infeed thread finished, shutting down.
INFO:tensorflow

In [27]:
fw.anim.show_input_func(train_input_func, n_img=20, converter=reverse_normalizer)

In [28]:
fw.io.create_clean_dir(work_dir)